# Feuille de travaux pratiques. Formules de quadrature interpolatoires

In [ ]:
# chargement des bibliothèques
import numpy as np

%matplotlib inline
import matplotlib.pyplot as plt

On s'intéresse dans cette feuille à l'une des applications les plus importante de l'interpolation polynomiale : les *formules de quadrature interpolatoires*.

## Exercice 1 (convergence des formules de Newton-Cotes composées)
Soit $f$ une fonction réelle continue sur un intervalle $[a,b]$. Le but de cet exercice est de mesurer l'efficacité de [formules de quadrature de Newton-Cotes](https://fr.wikipedia.org/wiki/Formule_de_Newton-Cotes) composées classiques pour l'approximation de l'intégrale définie
$$
I(f)=\int_a^b f(x)\,\mathrm{d}x,
$$
pour différents choix fonction. En particulier, on souhaite observer l'influence de la régularité de la fonction sur la précision des formules.

**1.** Écrire trois fonctions, ayant chacune pour paramètres d'entrée la fonction $f$, les bornes $a$ et $b$ de l'intervalle, et un nombre entier non nul $m$ de subdivisions de l'intervalle, calculant une approximation $I_{m,n}(f)$ de $I(f)$ respectivement par les formules de quadrature de la [règle du point milieu](http://fr.wikipedia.org/wiki/M%C3%A9thode_du_point_m%C3%A9dian) (formule ouverte, $n=0$), de la [règle du trapèze](http://fr.wikipedia.org/wiki/M%C3%A9thode_des_trap%C3%A8zes) (formule fermée, $n=1$) et de la [règle de Simpson](http://fr.wikipedia.org/wiki/M%C3%A9thode_de_Simpson) (formule fermée, $n=2$) composées.

**2.** On considère le cas $f(x)=e^x$, $a=0$ et $b=1$. Au moyen des fonctions `logspace` de NumPy et `loglog` de Matplotlib, tracer le graphe de l'erreur $\vert I(f)-I_{m,n}(f)\vert$ en fonction du nombre de sous-intervalles pour chacune de ces trois formules, en faisant varier le nombre de sous-intervalles de $1$ à $10000$. Commenter les résultats.

**3.** Reprendre la question précédente pour $f(x)=\vert 3\,x^4-1\vert$, $a=0$ et $b=1$. Que constate-t-on? Comment procéder pour retrouver les ordres de convergence théoriques des formules dans ce cas ?

## Exercice 2 (Gauss-Legendre versus Clenshaw-Curtis, d'après L. N. Trefethen)

Cet exercice s'inspire de l'article [*``Is Gauss quadrature better than Clenshaw-Curtis?''*](https://doi.org/10.1137/060659831), dans lequel les convergences respectives des formules de quadrature interpolatoires de Gauss-Legendre et de Clenshaw-Curtis sont comparées sur des exemples.

Les [formules de quadrature de Gauss](https://fr.wikipedia.org/wiki/M%C3%A9thodes_de_quadrature_de_Gauss) sont obtenues en choisissant les n&oelig;uds de quadrature de manière à maximiser leur degré d'exactitude. Elles ont été introduites par Gauss en 1814 et ont été largement utilisées depuis que les ordinateurs et des algorithmes permettent la détermination numérique de leurs n&oelig;uds et poids, ainsi que l'évaluation numérique des intégrand en des nombres irrationnels. On peut les diviser en différentes familles qui se distinguent d'une part par le domaine d'intégration et la fonction de pondération dans l'intégrand considérés, et d'autre part par leur lien avec une famille de polynômes orthogonaux. La famille des *formules de Gauss-Legendre* correspond à une intégration sur l'intervalle $[-1,1]$ avec une fonction de pondération égale à $1$. Pour tout entier naturel $n$, les $n+1$ n&oelig;uds d'une formule de Gauss-Legendre sont les racines du [polynôme de Legendre](https://fr.wikipedia.org/wiki/Polyn%C3%B4me_de_Legendre) de degré $n+1$, chaque poids pouvant s'exprimer en fonction du n&oelig;ud correspondant et de la dérivée première du polynôme de Legendre de degré $n+1$. Une telle formule a un degré d'exactitude égal à $2n+1$.

Les méthodes actuellement les plus efficaces pour le calcul des n&oelig;uds et poids reposent sur l'utilisation de la méthode de Newton-Raphson, de formules asymptotiques et de diverses optimisations spécifiques à ce problème et ont un coût de l'ordre de $O(n)$ opérations (voir par exemple [cet article](https://doi.org/10.1137%2F120889873)). Une autre manière de procéder est d'utiliser la méthode proposée par Golub et Welsch en 1969, qui ramène la détermination à la résolution d'un problème aux valeurs propres pour une matrice tridiagonale symétrique (liée à la relation de récurrence à trois termes satisfaite par les polynômes de Legendre) et possède un coût de l'ordre de $O(n^2)$ opérations (voir [cet article](https://doi.org/10.1090%2FS0025-5718-69-99647-1)).

La fonction `gauss_legendre_quadrature` ci-dessous propose une mise-en-oeuvre de la formule de Gauss-Legendre à $n+1$ n&oelig;uds basée sur la méthode de Golub et Welsch.

In [ ]:
from scipy import linalg

def gauss_legendre_quadrature(f,n):
# approximation de l'intégrale de la fonction f sur l'intervalle [-1,1] par la formule de quadrature de Gauss-Legendre à n+1 noeuds
# le calcul des noeuds et poids de la formule est fait pas la méthode de Golub et Welsch
    n=int(n)
    beta=1./(4.-(1.*np.arange(1,n+1))**(-2)) # coefficients de la relation de récurrence à trois termes
    val,vect=linalg.eigh_tridiagonal(np.zeros(n+1),np.sqrt(beta)) # résolution du problème aux valeurs propres
    p=np.argsort(val) # tri des valeurs propres
    x=val[p] # noeuds de quadrature
    w=2*vect[0,p]**2 # poids de quadrature
    return np.dot(w,f(x))


Les [formules de quadrature de Clenshaw-Curtis](https://fr.wikipedia.org/wiki/M%C3%A9thode_de_quadrature_de_Clenshaw-Curtis), introduites en 1960, sont basées sur une approximation de l'intégrand par un interpolant polynomial aux extrema du [polynôme de Chebyshev de première espèce](https://fr.wikipedia.org/wiki/Polyn%C3%B4me_de_Tchebychev) de degré adéquat. La formule de Clenshaw-Curtis à $n+1$ points possède ainsi un degré d'exactitude égal à $n$. Ses poids peuvent être calculés de manière efficace via une [tranformée en cosinus discrète](https://fr.wikipedia.org/wiki/Transform%C3%A9e_en_cosinus_discr%C3%A8te) de type I, avec un côut de l'ordre de $O(n\log(n))$ opérations en faisant appel un algorithme de [transformation de Fourier rapide](https://fr.wikipedia.org/wiki/Transformation_de_Fourier_rapide).

La fonction `clenshaw_curtis_quadrature` ci-dessous propose une mise-en-oeuvre de la formule de Clenshaw-Curtis à $n+1$ n&oelig;uds. Celle-ci n'utilise pas cette technique et posséde un coût de l'ordre de $O(n^2)$ opérations arithmétiques.

In [ ]:
def clewshaw_curtis_quadrature(f,n):
# approximation de l'intégrale de la fonction f sur l'intervalle [-1,1] par la formule de quadrature de Clenshaw-Curtis à n+1 noeuds
    n=int(n)
    x=np.cos(np.pi*np.arange(n+1)/n) # noeuds de quadrature
    w = np.ones ( n+1 )
    for i in range(n+1):
        for j in range(1,int(n/2)+1):
            if (2*j==n):
                b=1.
            else:
                b=2.
            w[i]=w[i]-b*np.cos(2.*j*i*np.pi/n)/(4.*j**2-1.)
    w[0],w[1:n],w[n]= w[0]/n,2.0* w[1:n]/n,w[n]/n # poids de quadrature
    return np.dot(w,f(x))

 **1.** Réaliser une comparaison expérimentale de la précision des formules de quadrature de Gauss-Legendre et de Clenshaw-Curtis en considérant successivement les intégrands suivants

 - $f(x)=x^{20}$,
 - $f(x)=e^x$,
 - $f(x)=e^{-x^2}$,
 - $f(x)=\frac{1}{1+16x^2}$,
 - $f(x)=e^{-\frac{1}{x^2}}$,
 - $f(x)=\lvert x\rvert^3$,
 
et un nombre de n&oelig;uds de quadrature allant de $1$ à $30$. On tracera les graphes de l'erreur $\vert I(f)-I_{n}(f)\vert$ en fonction de l'entier $n$ pour chacune des familles en se servant de la fonction `semilogy` de Matplotlib. 

**2.** Commenter les résultats obtenus.

## Exercice bonus (méthode de Romberg)

On considère l'utilisation de la règle du trapèze composée associée à une subdivision dyadique de l'intervalle $[a,b]$ pour le calcul de l'intégrale $I(f)$ de
l'exercice précédent. En supposant la fonction $f$ suffisamment régulière et en posant $H=\frac{b-a}{2^k}$, avec $k$ un entier naturel.

On peut montrer à partir de la [formule d'Euler-Maclaurin](https://fr.wikipedia.org/wiki/Formule_d%27Euler-Maclaurin) que l'erreur vérifie
$$
I(f)-I_{2^k,1}(f)=c_1\,H^2+c_2\,H^4+\dots,
$$
où les coefficients $c_k$ ne dépendent pas de $H$ et où seules les puissances paires apparaissent dans le développement. On peut exploiter cette propriété pour supprimer un à un les termes du développement, et ainsi obtenir de meilleures approximations de l'intégrale $I(f)$.

Posons $R_{k,0}=I_{2^k,1}(f)$. À partir d'une estimation de l'intégrale pour une subdivision de taille $\frac{H}{2}$, notée $R_{k+1,0}(=I_{2^{k+1},1}(f))$, l'utilisation du [procédé d'extrapolation de Richardson](https://fr.wikipedia.org/wiki/Extrapolation_de_Richardson) permet d'éliminer le premier terme du développement en considérant l'approximation fournie par la quantité
$$
R_{k+1,1}=R_{k+1,0}+\frac{1}{3}(R_{k+1,0}-R_{k,0})=\frac{1}{3}(4\,R_{k+1,0}-R_{k,0}),
$$
conduisant ainsi à une erreur d'ordre quatre en $H$.

Le procédé appelé [méthode de Romberg](https://fr.wikipedia.org/wiki/M%C3%A9thode_de_Romberg) pour l'évaluation approchée de $I(f)$ consiste en l'application répétée de cette opération à partir de la valeur $k=0$.

**1.** Écrire une fonction `romberg`, ayant pour arguments d'entrée une fonction $f$, les bornes $a$ et $b$ de l'intervalle, un nombre d'extrapolations maximal $N$ et une tolérance $\varepsilon$, renvoyant la valeur de l'approximation $R_{k,k}$ telle que $|R_{k,k}-R_{k-1,k-1}|\leq\varepsilon$, avec $0\leq k\leq N$, ou bien $k=N$. Pour cela, on construira un tableau contenant les valeurs extrapolées $R_{k,m}$, $0\leq m\leq k\leq N$, dont les éléments satisfont la relation de récurrence
$$
R_{k,m}=R_{k,m-1}+\frac{1}{4^m-1}\left(R_{k,m-1}-R_{k-1,m-1}\right),\ 1\leq m\leq k\leq N.
$$
Les approximations successives de $R_{k,k}$ construites par la méthode de Romberg se trouvent alors sur la diagonale du tableau et les éléments de la première colonne du tableau sont tels que $R_{k,0}=I_{2^k,1}(f)$, $k=0,\dots,N$.

**2.** Utiliser cette fonction pour calculer des approximations de l'intégrale $I(f)$ dans les cas suivants :
* $f(x)=x^3$, $a=0$, $b=1$,
* $f(x)=\frac{1}{x}$, $a=1$, $b=2$,
* $f(x)=\sin(x)$, $a=0$, $b=\pi$,
* $f(x)=x\sin(\sqrt{x})$, $a=0$, $b=3$,
* $f(x)=e^{-x^2}$, $a=0$, $b=1$.